## Import statments and basic functions

In [30]:
import pandas as pd 
import numpy as np # type: ignore
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import math

from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
pd.set_option('display.max_rows', 50000)
pd.set_option('display.max_columns', 50000)
pd.set_option('display.width', 100000)

In [8]:
data_0 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-4-island-data-bottle\prices_round_4_day_1.csv', sep = ';')
data_1 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-4-island-data-bottle\prices_round_4_day_2.csv', sep = ';')
data_2 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-4-island-data-bottle\prices_round_4_day_3.csv', sep = ';')

data = pd.concat([data_0, data_1, data_2], axis=0)
data['timestamp'] += 1e6 * (data['day'] - 1)

## splitting into coconut and its options
data_coco = data[data['product'] == 'COCONUT']
data_coco.reset_index(drop=True, inplace=True)

data_opts = data[data['product'] == 'COCONUT_COUPON']
data_opts.reset_index(drop=True, inplace=True)

data_1.head()

day  timestamp         product  bid_price_1  bid_volume_1  bid_price_2  bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  profit_and_loss
0    2          0         COCONUT      10135.0         150.0      10134.0          64.0          NaN           NaN        10136           150      10137.0          64.0          NaN           NaN    10135.5              0.0
1    2          0  COCONUT_COUPON        682.0          38.0          NaN           NaN          NaN           NaN          683            38          NaN           NaN          NaN           NaN      682.5              0.0
2    2        100  COCONUT_COUPON        681.0          19.0        680.0          20.0          NaN           NaN          682            39          NaN           NaN          NaN           NaN      681.5              0.0
3    2        100         COCONUT      10134.0         150.0          NaN           NaN          NaN           NaN        10136           106      10137.0          44.0          NaN           NaN    10135.0              0.0
4    2        200         COCONUT      10135.0         136.0      10134.0          55.0          NaN           NaN        10136           136      10137.0          55.0          NaN           NaN    10135.5              0.0

In [9]:
data_coco['diff'] = data_coco['mid_price'] - data_opts['mid_price']
data_opts['diff'] = data_coco['mid_price'] - data_opts['mid_price']

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\2611659925.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\2611659925.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [14]:
def add_spread(data):
    data['spread'] = data['ask_price_1'] - data['bid_price_1']
    data.reset_index(drop=True, inplace=True)

def add_pct_change(data):
    data['change'] = ((data['mid_price'] - data['mid_price'].shift(1)) / data['mid_price'] ) * 1e2

def add_ret(df, periods = [1, 5, 10, 30, 60, 300]):
    for period in periods:
        df[f'ret_{period}'] = df['mid_price'].pct_change(period).shift(-period) * 1e4
    

add_spread(data_coco)
add_spread(data_opts)

add_pct_change(data_opts)
add_pct_change(data_coco)

add_ret(data_coco)
add_ret(data_opts)

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\3233629454.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\3233629454.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\3233629454.py:10: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-

In [22]:
def plot_price(data, skip = 1):
    fig = go.Figure()

    # Add SUNLIGHT trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['bid_price_1'], name='bid_price_1'))

    # Add HUMIDITY trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['bid_price_2'], name='bid_price_2'))

    # Add ORCHIDS trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['ask_price_1'], name='ask_price_1'))

    # Add export target trace   
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['ask_price_2'], name='ask_price_2'))

    # fig.add_trace(go.Scatter(x=data['timestamp'], y=data['IMPORT_TARIFF'], name='IMPORT_TARIFF', yaxis='y5'))
    if(skip != 1):
        fig.add_trace(go.Scatter(x=data['timestamp'], y=data['diff'], name='difference'))

    
    # Update layout
    fig.update_layout(title='PRICE',
                    xaxis_title='Timestamp',
                    yaxis=dict(title='SUNLIGHT', side='left'))
                    

    # Show the plot
    fig.show()

plot_price(data_coco)
plot_price(data_opts)

## Black scholes model

### Calculating volatility (scaled)

In [26]:
a_volatility = 0

mean = data_coco['change'].mean()
std_dev = data_coco['change'].std()

a_volatility = std_dev * np.sqrt(250)
print(a_volatility)

0.16276192425237893


In [27]:
a_volatility1 = 0

mean = data_coco['change'][:10000].mean()
std_dev = data_coco['change'][:10000].std()

a_volatility1 = std_dev * np.sqrt(250)
print(a_volatility1)

0.16340227557747847


In [28]:
a_volatility2 = 0

mean = data_coco['change'][10000:20000].mean()
std_dev = data_coco['change'][10000:20000].std()

a_volatility2 = std_dev * np.sqrt(250)
print(a_volatility2)

0.16199862285647118


In [56]:
a_volatility2 = 0

mean = data_coco['change'][20000:30000].mean()
std_dev = data_coco['change'][20000:30000].std()

a_volatility3 = std_dev * np.sqrt(250)
print(a_volatility3)

0.1628629616722224


### Black scholes definition


In [31]:
from scipy.stats import norm

def black_scholes_call(S, X, T, r, sigma):
    d1 = (math.log(S / X) + (r + 0.5 * sigma ** 2) * T) / (sigma * math.sqrt(T))
    d2 = d1 - sigma * math.sqrt(T)
    call_price = S * norm.cdf(d1) - X * math.exp(-r * T) * norm.cdf(d2)
    return call_price

In [49]:
## grid search for best parameters, of S and r

def grid_search(data_stock, data_option, T, sigma):
    best_params = (0, 0)
    best_score = 1e9

    for r in (-0.0, 0.08, 0.001):
        score = 0
        # for i in range(len(data)):
        score += (data_option['mid_price'][0] - black_scholes_call(10000, data_stock['mid_price'][0], T, r, sigma)) ** 2
        if score < best_score:
            best_score = score
            best_params = (r)
            # print(S)
            print(f'Best score: {best_score}, Best params: {best_params}')
    return best_params

best_params = grid_search(data_coco, data_opts, 1, a_volatility)

print(best_params)

Best score: 123.43456452214899, Best params: -0.0
-0.0


In [39]:
data_opts.head()

day  timestamp         product  bid_price_1  bid_volume_1  bid_price_2  bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  profit_and_loss    diff  spread    change      ret_1      ret_5     ret_10      ret_30     ret_60     ret_300
0    1        0.0  COCONUT_COUPON        637.0          39.0          NaN           NaN          NaN           NaN          638            39          NaN           NaN          NaN           NaN      637.5              0.0  9362.5     1.0       NaN   0.000000   0.000000 -15.686275 -109.803922  62.745098 -203.921569
1    1      100.0  COCONUT_COUPON        637.0          33.0          NaN           NaN          NaN           NaN          638            33          NaN           NaN          NaN           NaN      637.5              0.0  9362.0     1.0  0.000000   0.000000 -15.686275 -31.372549  -47.058824  78.431373 -203.921569
2    1      200.0  COCONUT_COUPON        637.0          42.0          NaN           NaN          NaN           NaN          638            42          NaN           NaN          NaN           NaN      637.5              0.0  9361.0     1.0  0.000000  15.686275  31.372549 -31.372549  -47.058824  78.431373 -188.235294
3    1      300.0  COCONUT_COUPON        638.0          30.0          NaN           NaN          NaN           NaN          639            30          NaN           NaN          NaN           NaN      638.5              0.0  9361.0     1.0  0.156617 -15.661707 -31.323414 -62.646829  -62.646829  62.646829 -187.940486
4    1      400.0  COCONUT_COUPON        637.0          33.0          NaN           NaN          NaN           NaN          638            33          NaN           NaN          NaN           NaN      637.5              0.0  9361.0     1.0 -0.156863   0.000000 -47.058824 -47.058824  -62.745098  78.431373 -141.176471

In [58]:
data_coco['bs_price'] = 0
data_opts['bs_price'] = 0   
for i in range(10000):
    data_opts['bs_price'][i] = black_scholes_call(10000, data_coco['mid_price'][i], 1, best_params, a_volatility)
    data_opts['bs_price'][i + 10000] = black_scholes_call(10000, data_coco['mid_price'][i], 249/250, best_params, a_volatility)
    data_opts['bs_price'][i + 20000] = black_scholes_call(10000, data_coco['mid_price'][i], 248/250, best_params, a_volatility)

data_coco['bs_price'] = data_opts['bs_price']

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\1872692863.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\1872692863.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\1872692863.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-vers

In [60]:
data_opts['alpha'] = data_opts['mid_price'] - data_opts['bs_price']

C:\Users\ayush\AppData\Local\Temp\ipykernel_5800\1227610030.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [61]:
def print_corrs(df, alphas, rets = ['ret_10', 'ret_30', 'ret_300', 'ret_5']):
# def print_corrs(df, alphas, rets = ['ret_10', 'ret_30', 'iv_10']):
# def print_corrs(df, alphas, rets = ['tick_10', 'tick_30', 'tick_60', 'tick_300']):
# def print_corrs(df, alphas, rets = ['ret_60', 'ret_300', 'iv_60']):
    msg = "                                      "
    for ret in rets:
        msg += f"{ret:>8s}"
    print(msg)
    for alpha in alphas:
        msg = f"{alpha:30s} corr -> "
        for ret in rets:
            msg += f"{df[alpha].corr(df[ret])*100:7.2f} "
        print(msg)
    print()

def print_buckets(df, alphas, rets = ['ret_10', 'ret_5', 'ret_30', 'ret_300'], aggfunc = ['mean', 'median', 'count'], buckets = 5):
# def print_buckets(df, alphas, rets = ['ret_10', 'ret_30', 'iv_10'], aggfunc = ['mean', 'median', 'count']):
# def print_buckets(df, alphas, rets = ['tick_10', 'tick_30', 'tick_60', 'tick_300'], aggfunc = ['mean', 'median', 'count']):
# def print_buckets(df, alphas, rets = ['ret_60', 'ret_300', 'iv_60'], aggfunc = ['mean', 'median', 'count']):
    for alpha in alphas:
        msg = df.pivot_table(index = pd.qcut(df[alpha],buckets,duplicates='drop'), values=rets, aggfunc=aggfunc)
        print(msg)

In [62]:
print_corrs(data_opts, ['alpha'])
print_buckets(data_opts, ['alpha'], buckets = 10)

                                        ret_10  ret_30 ret_300   ret_5
alpha                          corr ->   -3.97   -6.93  -17.75   -2.82 

                        mean                                      median                               count                     
                      ret_10     ret_30     ret_300     ret_5     ret_10     ret_30     ret_300 ret_5 ret_10 ret_30 ret_300 ret_5
alpha                                                                                                                            
(-94.983, -63.055]  9.299049  27.439522  192.287315  4.745646  16.708438  33.472803  196.604111   0.0   3000   3000    3000  3000
(-63.055, -49.369] -0.768874  -2.626270  -33.254052  0.006432   0.000000   0.000000  -51.546430   0.0   3000   3000    3000  3000
(-49.369, -35.768] -1.145874  -2.189347  -58.912950 -1.056523   0.000000   0.000000  -84.317092   0.0   3000   3000    3000  3000
(-35.768, -13.627] -4.952839 -17.486284  -64.767712 -2.198544   0.000000 -17